# Ant Colony Optimisation Example

## 1. Initlialisation

#### Get distance matrix

In [1]:
# Create distance matrix (excluding distance from each point to itself)
import random
import xml.etree.ElementTree as ET
tree = ET.parse('burma14.xml')
root = tree.getroot()

d = []

for vertex in root.iter('vertex'):
    temp = [0]*14
    for edge in vertex.iter('edge'):
        temp[int(edge.text)] = (float(edge.get('cost')))
    d.append(temp)
    
print(d)

[[0, 153.0, 510.0, 706.0, 966.0, 581.0, 455.0, 70.0, 160.0, 372.0, 157.0, 567.0, 342.0, 398.0], [153.0, 0, 422.0, 664.0, 997.0, 598.0, 507.0, 197.0, 311.0, 479.0, 310.0, 581.0, 417.0, 376.0], [510.0, 422.0, 0, 289.0, 744.0, 390.0, 437.0, 491.0, 645.0, 880.0, 618.0, 374.0, 455.0, 211.0], [706.0, 664.0, 289.0, 0, 491.0, 265.0, 410.0, 664.0, 804.0, 1070.0, 768.0, 259.0, 499.0, 310.0], [966.0, 997.0, 744.0, 491.0, 0, 400.0, 514.0, 902.0, 990.0, 1261.0, 947.0, 418.0, 635.0, 636.0], [581.0, 598.0, 390.0, 265.0, 400.0, 0, 168.0, 522.0, 634.0, 910.0, 593.0, 19.0, 284.0, 239.0], [455.0, 507.0, 437.0, 410.0, 514.0, 168.0, 0, 389.0, 482.0, 757.0, 439.0, 163.0, 124.0, 232.0], [70.0, 197.0, 491.0, 664.0, 902.0, 522.0, 389.0, 0, 154.0, 406.0, 133.0, 508.0, 273.0, 355.0], [160.0, 311.0, 645.0, 804.0, 990.0, 634.0, 482.0, 154.0, 0, 276.0, 43.0, 623.0, 358.0, 498.0], [372.0, 479.0, 880.0, 1070.0, 1261.0, 910.0, 757.0, 406.0, 276.0, 0, 318.0, 898.0, 633.0, 761.0], [157.0, 310.0, 618.0, 768.0, 947.0, 593

#### Compute Heuristic Matrix

In [2]:
# Initial Hueristic Matrix
H = [[ round(1/d[i][j],4) if i != j else 0 for j in range(14)] for i in range(14)]

print(H)

[[0, 0.0065, 0.002, 0.0014, 0.001, 0.0017, 0.0022, 0.0143, 0.0063, 0.0027, 0.0064, 0.0018, 0.0029, 0.0025], [0.0065, 0, 0.0024, 0.0015, 0.001, 0.0017, 0.002, 0.0051, 0.0032, 0.0021, 0.0032, 0.0017, 0.0024, 0.0027], [0.002, 0.0024, 0, 0.0035, 0.0013, 0.0026, 0.0023, 0.002, 0.0016, 0.0011, 0.0016, 0.0027, 0.0022, 0.0047], [0.0014, 0.0015, 0.0035, 0, 0.002, 0.0038, 0.0024, 0.0015, 0.0012, 0.0009, 0.0013, 0.0039, 0.002, 0.0032], [0.001, 0.001, 0.0013, 0.002, 0, 0.0025, 0.0019, 0.0011, 0.001, 0.0008, 0.0011, 0.0024, 0.0016, 0.0016], [0.0017, 0.0017, 0.0026, 0.0038, 0.0025, 0, 0.006, 0.0019, 0.0016, 0.0011, 0.0017, 0.0526, 0.0035, 0.0042], [0.0022, 0.002, 0.0023, 0.0024, 0.0019, 0.006, 0, 0.0026, 0.0021, 0.0013, 0.0023, 0.0061, 0.0081, 0.0043], [0.0143, 0.0051, 0.002, 0.0015, 0.0011, 0.0019, 0.0026, 0, 0.0065, 0.0025, 0.0075, 0.002, 0.0037, 0.0028], [0.0063, 0.0032, 0.0016, 0.0012, 0.001, 0.0016, 0.0021, 0.0065, 0, 0.0036, 0.0233, 0.0016, 0.0028, 0.002], [0.0027, 0.0021, 0.0011, 0.0009, 0.00

#### Initialise Pheromone Matrix

## 2. Creating base methods

#### Node Traversing Methods

In [3]:
def remove_current_city(city, H):
    """
    Removes current node from hueristic matrix

    :param city: the current node
    :param H: hueristic matrix
    :return: new heuristic matrix
    """ 
    for i in range(14):
        for j in range(14):
            if j != city and i != j and H[i][j] != 0:
                H[i][j] = round(1/d[i][j],4)
            else:
                H[i][j] = 0
    return H
            

def create_probs(city, H, T, alpha, beta):
    """
    Create probability matrix using heuristic and pheromones

    :param city: the current node
    :param H: hueristic matrix
    :param T: pheromone matrix
    :param alpha: alpha hyper parameter
    :param beta: beta hyper parameter
    :return: probability matrix
    """ 
    N = [None]*14
    P = [None]*14
    den = 0

    # for each value in row of current city, plug number into formula x^alpha * y^beta
    for j in range(14):
        N[j] = T[city][j] **alpha * H[city][j] **beta
        den += N[j]

    for j in range(14):
        P[j] = N[j]/den
    
    return P


# Cumulative probabilities to find next city
def find_next_city(P, city):
    """
    Determines the next node for an ant to go to

    :param P: probability matrix
    :param city: current node
    :return: next node
    """ 
    rand = random.random()
    CP = 0

    for i in range(14):
        CP += P[i]
        if CP >= rand:
            return i


#### Create and run ants methods

In [4]:
import copy

def create_ants(num, alpha, beta):
    """
    Create set of ants

    :param num: number of ants to create
    :param alpha: alpha hyper parameter
    :param beta: beta hyper parameter
    :return: list of ant objects
    """ 
    # List to hold ants
    Ants = []

    # Initial probabilities
    P = create_probs(0, copy.deepcopy(H), copy.deepcopy(T), alpha, beta)

    # Create ants
    for i in range(num):
        Ants.append({
            "Name": (i+1),
            "H": copy.deepcopy(H),
            "T": copy.deepcopy(T),
            "P": copy.deepcopy(P),
            "Length": 0,
            "Path" : [0]
        })
    return Ants
        
def run_ants(start, Ants, alpha, beta):
    """
    Run the ants over the nodes storing a path and length for each

    :param start: starting node
    :param Ants: list of ant objects
    :param alpha: alpha hyper parameter
    :param beta: beta hyper parameter
    :return: void
    """ 
        
    # For each ant
    for ant in Ants:

        # Start city
        current_city = start
        print(f'NEXT ANT. City: {current_city}, Ant: {ant["Name"]}, Path: {ant["Path"]}')

        # Go to every node
        for i in range(13):
            # Remove this city from heuristics
            ant["H"] = remove_current_city(current_city, ant["H"])

            # Create probabilities
            ant["P"] = create_probs(current_city, ant["H"], ant["T"], alpha, beta)

            # Get next city to go to
            temp = current_city
            current_city = find_next_city(ant["P"], current_city)

            # Update length
            ant["Length"] += d[temp][current_city]
            print(f'City is {current_city}')

            # Update path
            ant["Path"].append(current_city)
            
        print(f'Path: {ant["Path"]}')
        print(f'Length {ant["Length"]}')
        print("\n------------------------\n")

#### Evapourate and deposit methods

In [5]:
# Evapourate Pheromones
def evapourate(rho):
    """
    Evapourate pheromones

    :param rho: evapouration rate
    :return: void
    """ 
    for i in range(14):
        for j in range(14):
            T[i][j] = (1 - rho) * T[i][j]

def pheromone_update(Ants, Q):
    """
    Updates pheromones for acs approach

    :param Ants: list of ant objects
    :param Q: hyper parameter to scale pheromones
    :return: void
    """ 
    
    # Loop through every ant
    for ant in Ants:
        # Determine the amount to deposit
        delta = Q/ant["Length"]

        # Deposit on each path taken
        for i in range(13):
            T[ant["Path"][i]][ant["Path"][i+1]] += delta
            
def pheromone_update_mmas(Ants, Q, global_best, upper_limit, lower_limit, mmas_type):
    """
    Updates pheromones for mmas approach

    :param Ants: list of ant objects
    :param Q: hyper parameter to scale pheromones
    :param global_best: global best path and length
    :param upper_limit: upper limit for pheromones
    :param lower_limit: lower limit for pheromones
    :param mmas_type: type of mmas (local or global)
    :return: void
    """ 
    
    # Global or Local mmas
    if mmas_type == "global":
        best_length = global_best
    elif mmas_type == "local":
        # Find local best
        best_length = find_best(Ants)["Length"]
           
    # Loop through every ant
    for ant in Ants:
        # If better than or equal to global/local best length then deposit
        if ant["Length"] <= best_length:
            # Determine the amount to deposit
            delta = Q/ant["Length"]

            # Limits for pheromone values
            if delta > upper_limit: delta = upper_limit
            elif delta < lower_limit: delta = lower_limit
                
            # Deposit on each path taken
            for i in range(13):
                T[ant["Path"][i]][ant["Path"][i+1]] += delta
        
def pheromone_update_elitist(Ants, Q, global_best):
    """
    Updates pheromones for elitist approach

    :param Ants: list of ant objects
    :param Q: hyper parameter to scale pheromones
    :param global_best: global best path and length
    :return: void
    """ 
    
    # Find local best
    local_best = find_best(Ants)
    
    # If local is worse than global then deposit global
    if local_best["Length"] < global_best["Length"]:
        
        # Determine the amount to deposit
        delta = Q/global_best["Length"]
        
        # Deposit on each path taken
        for i in range(13):
            T[global_best["Path"][i]][global_best["Path"][i+1]] += delta
    
    # Loop through every ant
    for ant in Ants:
        # Determine the amount to deposit
        delta = Q/ant["Length"]

        # Deposit on each path taken
        for i in range(13):
            T[ant["Path"][i]][ant["Path"][i+1]] += delta

        
            
        




## Running the optimisation

In [6]:
# Define Global Pheromones (random by defaultbut overridden if needed)
T = [[random.random() for j in range(14)] for i in range(14)]

# Main loop
def run_optimisation(num_ants, num_iterations, starting_city, Q, mmas, approach_type, rho, alpha, beta):
    """
    Runs the optimisation

    :param num_ants: number of ants
    :param num_iterations: number of iterations
    :param starting_city: starting node
    :param Q: hyper parameter to scale pheromones
    :param mmas: mmas properties
    :param approach_type: type of approach (acs, mmas, elitist)
    :param rho: evapouration rate
    :param alpha: alpha hyper parameter
    :param beta: beta hyper parameter
    :return: best solution (path and length)
    """ 
    
    Ants = []
    for i in range(num_iterations):
        # Create and run ants
        Ants = create_ants(num_ants, alpha, beta)
        run_ants(starting_city, Ants, alpha, beta)
        
        # Find local best
        local_best = find_best(Ants)
        
        # Set global best
        if i == 0 or (local_best["Length"] < global_best["Length"]):
            global_best = local_best
        

        # Check approach variation
        match approach_type:
            case "mmas":
                # Use upper limit pheromones and limited depositing
                T = [[mmas["upper"] for j in range(14)] for i in range(14)]
                pheromone_update_mmas(Ants, Q, global_best["Length"], mmas["upper"], mmas["lower"], mmas["type"])
            case "elitist":
                # Use random pheromones and global best always deposits
                pheromone_update_elitist(Ants, Q, global_best)
            case "acs":
                # Use random pheromones and no limits on deposits
                pheromone_update(Ants, Q)
        
        # Evapourate pheromones
        evapourate(rho)
    
    # Return best path and length in last set of ants
    return find_best(Ants)

def find_best(Ants):
    """
    Find the best solution

    :param Ants: list of ant objects
    :return: best solution (path and length)
    """ 
    
    # Find the smallest length
    smallest = Ants[0]["Length"]
    path = Ants[0]["Path"]
    for ant in Ants:
        if ant["Length"] < smallest:
            smallest = ant["Length"]
            path = ant["Path"]

    return {"Length": smallest, "Path": path}

## Experiments

In [7]:
# Experimental parameters
num_ants = 100
Q = 1
rho = 0.5
alpha = 1
beta = 2
approach_type = "mmas" # ("mmas", "elitist", "acs")
mmas = {"upper": 1, "lower": 0, "type": "global"} #(type: "global", "local")


# Base parameters
num_iterations = round(10_000 / num_ants)
starting_city = 0

solution = run_optimisation(num_ants, num_iterations, starting_city, Q, mmas, approach_type, rho, alpha, beta)

print(f'Solution:\nLength: {solution["Length"]}\nPath: {solution["Path"]}')

NEXT ANT. City: 0, Ant: 1, Path: [0]
City is 1
City is 2
City is 8
City is 10
City is 7
City is 9
City is 13
City is 3
City is 5
City is 11
City is 6
City is 12
City is 4
Path: [0, 1, 2, 8, 10, 7, 9, 13, 3, 5, 11, 6, 12, 4]
Length 4079.0

------------------------

NEXT ANT. City: 0, Ant: 2, Path: [0]
City is 7
City is 1
City is 10
City is 8
City is 4
City is 5
City is 3
City is 6
City is 13
City is 2
City is 11
City is 12
City is 9
Path: [0, 7, 1, 10, 8, 4, 5, 3, 6, 13, 2, 11, 12, 9]
Length 4410.0

------------------------

NEXT ANT. City: 0, Ant: 3, Path: [0]
City is 1
City is 8
City is 10
City is 7
City is 11
City is 5
City is 4
City is 13
City is 6
City is 12
City is 2
City is 3
City is 9
Path: [0, 1, 8, 10, 7, 11, 5, 4, 13, 6, 12, 2, 3, 9]
Length 4373.0

------------------------

NEXT ANT. City: 0, Ant: 4, Path: [0]
City is 1
City is 8
City is 10
City is 7
City is 9
City is 13
City is 3
City is 5
City is 11
City is 12
City is 6
City is 2
City is 4
Path: [0, 1, 8, 10, 7, 9, 13, 3, 5

City is 5
City is 11
City is 13
City is 3
City is 4
City is 9
Path: [0, 7, 8, 10, 1, 6, 12, 2, 5, 11, 13, 3, 4, 9]
Length 4355.0

------------------------

NEXT ANT. City: 0, Ant: 94, Path: [0]
City is 7
City is 1
City is 12
City is 6
City is 5
City is 11
City is 3
City is 10
City is 8
City is 4
City is 13
City is 2
City is 9
Path: [0, 7, 1, 12, 6, 5, 11, 3, 10, 8, 4, 13, 2, 9]
Length 4782.0

------------------------

NEXT ANT. City: 0, Ant: 95, Path: [0]
City is 2
City is 13
City is 3
City is 7
City is 8
City is 10
City is 9
City is 1
City is 4
City is 6
City is 12
City is 11
City is 5
Path: [0, 2, 13, 3, 7, 8, 10, 9, 1, 4, 6, 12, 11, 5]
Length 4618.0

------------------------

NEXT ANT. City: 0, Ant: 96, Path: [0]
City is 8
City is 10
City is 9
City is 13
City is 2
City is 5
City is 11
City is 6
City is 12
City is 7
City is 4
City is 3
City is 1
Path: [0, 8, 10, 9, 13, 2, 5, 11, 6, 12, 7, 4, 3, 1]
Length 4519.0

------------------------

NEXT ANT. City: 0, Ant: 97, Path: [0]
City is 

City is 13
City is 2
City is 3
City is 10
City is 4
Path: [0, 8, 7, 12, 6, 5, 11, 9, 1, 13, 2, 3, 10, 4]
Length 4866.0

------------------------

NEXT ANT. City: 0, Ant: 59, Path: [0]
City is 7
City is 8
City is 10
City is 1
City is 4
City is 5
City is 11
City is 3
City is 12
City is 13
City is 2
City is 6
City is 9
Path: [0, 7, 8, 10, 1, 4, 5, 11, 3, 12, 13, 2, 6, 9]
Length 4403.0

------------------------

NEXT ANT. City: 0, Ant: 60, Path: [0]
City is 7
City is 8
City is 10
City is 1
City is 12
City is 4
City is 5
City is 11
City is 9
City is 13
City is 6
City is 2
City is 3
Path: [0, 7, 8, 10, 1, 12, 4, 5, 11, 9, 13, 6, 2, 3]
Length 4665.0

------------------------

NEXT ANT. City: 0, Ant: 61, Path: [0]
City is 10
City is 8
City is 5
City is 11
City is 6
City is 7
City is 9
City is 2
City is 12
City is 13
City is 3
City is 1
City is 4
Path: [0, 10, 8, 5, 11, 6, 7, 9, 2, 12, 13, 3, 1, 4]
Length 5364.0

------------------------

NEXT ANT. City: 0, Ant: 62, Path: [0]
City is 7
City is 

City is 11
City is 5
City is 4
City is 3
City is 9
Path: [0, 10, 8, 7, 1, 13, 2, 6, 12, 11, 5, 4, 3, 9]
Length 3954.0

------------------------

NEXT ANT. City: 0, Ant: 11, Path: [0]
City is 10
City is 8
City is 12
City is 11
City is 5
City is 4
City is 1
City is 9
City is 13
City is 6
City is 7
City is 3
City is 2
Path: [0, 10, 8, 12, 11, 5, 4, 1, 9, 13, 6, 7, 3, 2]
Length 5063.0

------------------------

NEXT ANT. City: 0, Ant: 12, Path: [0]
City is 1
City is 5
City is 3
City is 13
City is 6
City is 2
City is 9
City is 7
City is 8
City is 10
City is 11
City is 12
City is 4
Path: [0, 1, 5, 3, 13, 6, 2, 9, 7, 8, 10, 11, 12, 4]
Length 4970.0

------------------------

NEXT ANT. City: 0, Ant: 13, Path: [0]
City is 7
City is 8
City is 10
City is 9
City is 1
City is 5
City is 11
City is 6
City is 2
City is 13
City is 3
City is 12
City is 4
Path: [0, 7, 8, 10, 9, 1, 5, 11, 6, 2, 13, 3, 12, 4]
Length 3936.0

------------------------

NEXT ANT. City: 0, Ant: 14, Path: [0]
City is 1
City is 8

City is 7
City is 4
City is 5
City is 11
City is 6
City is 12
City is 2
City is 9
City is 1
City is 13
City is 3
Path: [0, 10, 8, 7, 4, 5, 11, 6, 12, 2, 9, 1, 13, 3]
Length 4462.0

------------------------

NEXT ANT. City: 0, Ant: 84, Path: [0]
City is 10
City is 8
City is 7
City is 13
City is 2
City is 5
City is 11
City is 6
City is 12
City is 4
City is 3
City is 1
City is 9
Path: [0, 10, 8, 7, 13, 2, 5, 11, 6, 12, 4, 3, 1, 9]
Length 3885.0

------------------------

NEXT ANT. City: 0, Ant: 85, Path: [0]
City is 1
City is 10
City is 8
City is 7
City is 13
City is 2
City is 3
City is 11
City is 5
City is 9
City is 6
City is 12
City is 4
Path: [0, 1, 10, 8, 7, 13, 2, 3, 11, 5, 9, 6, 12, 4]
Length 4219.0

------------------------

NEXT ANT. City: 0, Ant: 86, Path: [0]
City is 1
City is 10
City is 8
City is 5
City is 11
City is 3
City is 12
City is 7
City is 13
City is 2
City is 6
City is 4
City is 9
Path: [0, 1, 10, 8, 5, 11, 3, 12, 7, 13, 2, 6, 4, 9]
Length 4968.0

---------------------

...

City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 98, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 99, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 100, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 1, Path: [0

City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 46, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 47, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 48, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 49, Path: [0]
City is 7
City is 10
City is 

City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 28, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 29, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 30, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0



City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 21, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 22, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 23, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 24, Path: [0]
City is 

City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 98, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 99, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

NEXT ANT. City: 0, Ant: 100, Path: [0]
City is 7
City is 10
City is 8
City is 9
City is 1
City is 12
City is 6
City is 11
City is 5
City is 13
City is 2
City is 3
City is 4
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
Length 2954.0

------------------------

Solution:
Length: 2954.0
Path: [0, 7, 10, 8, 9, 1, 12, 6, 11, 5, 13, 2, 3, 4]
